# Temperatuur sensoren

In [1]:
import io
import os
import sys
import types
import numpy as np
import pandas as pd
import altair as alt

Sensor 1: item0060, item0061, item0062  
Sensor 2: item0063, item0064, item0065  
Sensor 2: item0066, item0067, item0068  


#df_g = GetMySQL.getSQL(poi,"item0054",props,"gas")
     

In [2]:
%run MakeNBImportAvailable.ipynb

In [3]:
from datetime import date
from datetime import datetime, timedelta
# import RetrieveData as rd_gn
# import knmi_gn_001 as gethdd
# import Process_Data_CH as prcs
import GetMySQL

importing Jupyter notebook from GetMySQL.ipynb


In [4]:
# settings = GetMySQL.readsettings()

In [5]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [6]:
def setpoi(nrdays):
    today = date.today()
    startday = today -timedelta(days=nrdays)
    endday = today + timedelta(days=1)
    # poi = pd.date_range(startday,today)
    poi = [startday,endday]
    poi  = [d.strftime('%Y-%m-%d') for d in poi]
    poi = ':'.join([poi[0],poi[1]])

    poi = GetMySQL.SetPOI(poi)
    return poi



In [7]:
poi = setpoi(2)

POI is :  {'start': '2022-12-09', 'end': '2022-12-12'}


In [8]:
sensors = pd.DataFrame({'s1':[60,61,62],
                        's2':[63,64,65],
                        's3':[66,67,68]})
sensors = pd.melt(sensors)
sensors['valuestr'] = sensors['value'].apply(lambda x: ''.join(['item00',str(x)]))

In [9]:
def read_temp_data(sensordf,poi):
    df = []
    props = GetMySQL.readsettings()
    for i,row in sensordf.iterrows():
        sr = row['valuestr']
        df.append(GetMySQL.getSQL(poi,sr,props,sr))
    
    df = pd.concat(df)
    
    return(df)
    

In [10]:
df = read_temp_data(sensors,poi)
df.shape

(36891, 3)

In [11]:
df = df.reset_index()

In [12]:
df['dy'] = pd.to_datetime(df['dy'], errors='coerce')

In [13]:
df['normalday'] = '2022-01-01'
df['normalday'] = df['normalday'] +' '+ df['datetime'].dt.hour.astype(str)+':'+df['datetime'].dt.minute.astype(str)
df['normalday'] = pd.to_datetime(df['normalday'])

In [14]:
df.head()

datetime  counter  variable         dy           normalday
0 2022-12-09 00:00:00    19.91  item0060 2022-12-09 2022-01-01 00:00:00
1 2022-12-09 00:01:00    19.93  item0060 2022-12-09 2022-01-01 00:01:00
2 2022-12-09 00:02:00    19.90  item0060 2022-12-09 2022-01-01 00:02:00
3 2022-12-09 00:03:00    19.87  item0060 2022-12-09 2022-01-01 00:03:00
4 2022-12-09 00:04:00    19.89  item0060 2022-12-09 2022-01-01 00:04:00

In [15]:
df = df.merge(sensors[['variable','valuestr']],left_on='variable', right_on='valuestr')


In [16]:
df.dtypes

datetime      datetime64[ns]
counter              float64
variable_x            object
dy            datetime64[ns]
normalday     datetime64[ns]
variable_y            object
valuestr              object
dtype: object

In [17]:
def plotdata(df,sensor,starthr=0,endhour=24):

    df=df[(df['datetime'].dt.hour<endhour)&(df['datetime'].dt.hour>=starthr)]
    wdth = 200
    source = df
    chart1a = alt.Chart(source[source['variable_y']==sensor]).mark_line(
            strokeWidth=1).encode(
            x=alt.X('normalday:T',
                axis=alt.Axis(title="tijd")),
            y=alt.Y("counter:Q",
                axis=alt.Axis(title="Temperaturen")),
        color=alt.Color('dy:N')
        ).properties(width=wdth,height=250).facet(
        facet='valuestr:N',
    columns=3,title='Temperaturen'
).interactive()

    

    display(chart1a)
    

In [18]:
# base = alt.Chart().mark_point().encode(
#     color='species:N'
# ).properties(
#     width=200,
#     height=200
# ).interactive()

# chart = alt.vconcat(data=df)
# for y_encoding in ['petalLength:Q', 'petalWidth:Q']:
#     row = alt.hconcat()
#     for x_encoding in ['sepalLength:Q', 'sepalWidth:Q']:
#         row |= base.encode(x=x_encoding, y=y_encoding)
#     chart &= row
# chart

In [24]:
plotdata(df,'s1',8,24)

alt.FacetChart(...)

In [22]:
plotdata(df,'s2')

alt.FacetChart(...)

In [21]:
plotdata(df,'s3',14,16)

alt.FacetChart(...)

In [21]:
def plotdata_all(df,sensorvars):
    wdth = 300
    source = df
    chart1a = alt.Chart(source[source['valuestr'].isin(sensorvars)],title='Temperaturen').mark_line(
            strokeWidth=1).encode(
            x=alt.X('normalday:T',
                axis=alt.Axis(title="tijd")),
            y=alt.Y("counter:Q",
                axis=alt.Axis(title="Temperaturen")),
        color=alt.Color('variable_y:N')
        ).properties(width=wdth,height=250).facet(facet='dy:N',
    columns=2
).interactive()

    display(chart1a)

In [22]:
df.head()

datetime  counter variable_x         dy           normalday  \
0 2022-12-08 00:00:00    20.05   item0060 2022-12-08 2022-01-01 00:00:00   
1 2022-12-08 00:01:00    20.04   item0060 2022-12-08 2022-01-01 00:01:00   
2 2022-12-08 00:02:00    20.03   item0060 2022-12-08 2022-01-01 00:02:00   
3 2022-12-08 00:03:00    20.04   item0060 2022-12-08 2022-01-01 00:03:00   
4 2022-12-08 00:04:00    20.01   item0060 2022-12-08 2022-01-01 00:04:00   

  variable_y  valuestr  
0         s1  item0060  
1         s1  item0060  
2         s1  item0060  
3         s1  item0060  
4         s1  item0060

In [23]:
df['valuestr'].unique()

array(['item0060', 'item0061', 'item0062', 'item0063', 'item0064',
       'item0065', 'item0066', 'item0067', 'item0068'], dtype=object)

In [24]:
plotdata_all(df[['variable_y','normalday','counter','valuestr','dy']],['item0060','item0063','item0066'])

alt.FacetChart(...)

In [26]:
temp_in=['item0060','item0063','item0066']

In [27]:
df[df['valuestr'].isin(temp_in)].groupby(['valuestr','dy']).mean()

counter
valuestr dy                   
item0060 2022-12-02  31.760104
         2022-12-03  30.430917
         2022-12-04  32.311246
item0063 2022-12-02  34.296236
         2022-12-03  35.063215
         2022-12-04  32.913166
item0066 2022-12-02  32.719021
         2022-12-03  33.251160
         2022-12-04  31.295337